In [1]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, AutoConfig, AutoModel

tokenizer = AutoTokenizer.from_pretrained('ku-nlp/bart-base-japanese')
base_model = AutoModelForSeq2SeqLM.from_pretrained('ku-nlp/bart-base-japanese')

In [2]:
import torch
rmt_model = torch.load('saved/tobyoki/bart-base-japanese/BaseModelWithRMT/pytorch_model.bin')
rmt_model

OrderedDict([('cls_token', tensor([0], device='cuda:0')),
             ('sep_token', tensor([2], device='cuda:0')),
             ('eos_token', tensor([2], device='cuda:0')),
             ('bos_token', tensor([0], device='cuda:0')),
             ('mem_token_ids',
              tensor([  0,   1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,  13,
                       14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,  26,  27,
                       28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,  39,  40,  41,
                       42,  43,  44,  45,  46,  47,  48,  49,  50,  51,  52,  53,  54,  55,
                       56,  57,  58,  59,  60,  61,  62,  63,  64,  65,  66,  67,  68,  69,
                       70,  71,  72,  73,  74,  75,  76,  77,  78,  79,  80,  81,  82,  83,
                       84,  85,  86,  87,  88,  89,  90,  91,  92,  93,  94,  95,  96,  97,
                       98,  99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111,
 

In [3]:
from config import RMTBartConfig
from model import BartRMTForPubmed

pre_seq_len=150
post_seq_len=0

rmt_config = RMTBartConfig(
    pre_seq_len=pre_seq_len,
    post_seq_len=post_seq_len,
    max_section_length=512+pre_seq_len+post_seq_len,
    max_source_length=512,
)

model = BartRMTForPubmed(
    base_model=base_model,
    config=rmt_config,
    tokenizer_name_or_path="ku-nlp/bart-base-japanese",
)
model

BartRMTForPubmed(
  (model): MBartForConditionalGeneration(
    (model): MBartModel(
      (shared): Embedding(32002, 768, padding_idx=1)
      (encoder): MBartEncoder(
        (embed_tokens): Embedding(32002, 768, padding_idx=1)
        (embed_positions): MBartLearnedPositionalEmbedding(1026, 768)
        (layers): ModuleList(
          (0-5): 6 x MBartEncoderLayer(
            (self_attn): MBartAttention(
              (k_proj): Linear(in_features=768, out_features=768, bias=True)
              (v_proj): Linear(in_features=768, out_features=768, bias=True)
              (q_proj): Linear(in_features=768, out_features=768, bias=True)
              (out_proj): Linear(in_features=768, out_features=768, bias=True)
            )
            (self_attn_layer_norm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
            (activation_fn): GELUActivation()
            (fc1): Linear(in_features=768, out_features=3072, bias=True)
            (fc2): Linear(in_features=3072, out_features

In [4]:
model.load_state_dict(rmt_model)

<All keys matched successfully>

In [5]:
model

BartRMTForPubmed(
  (model): MBartForConditionalGeneration(
    (model): MBartModel(
      (shared): Embedding(32002, 768, padding_idx=1)
      (encoder): MBartEncoder(
        (embed_tokens): Embedding(32002, 768, padding_idx=1)
        (embed_positions): MBartLearnedPositionalEmbedding(1026, 768)
        (layers): ModuleList(
          (0-5): 6 x MBartEncoderLayer(
            (self_attn): MBartAttention(
              (k_proj): Linear(in_features=768, out_features=768, bias=True)
              (v_proj): Linear(in_features=768, out_features=768, bias=True)
              (q_proj): Linear(in_features=768, out_features=768, bias=True)
              (out_proj): Linear(in_features=768, out_features=768, bias=True)
            )
            (self_attn_layer_norm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
            (activation_fn): GELUActivation()
            (fc1): Linear(in_features=768, out_features=3072, bias=True)
            (fc2): Linear(in_features=3072, out_features

In [28]:
inputs = """もう朝だね。
結局眠れなかったよ

眠剤も切れちゃったし…
明日病院行くからもらってこよう。

おなかが空いたんだけど、作るのがめんどくさかったからお湯をそそぐだけのカップ焼きそばを食べた。
こんなに消化が悪いもの、お腹壊すの分かってて食べる。。。

でも、その前に。。。
食道が痛い。。。
飲み込むだけで痛い。。。
食べ終わっても痛い。。。

手術の影響なのか、ココになんか新たな何かがあるのか。。。

傷の痛み止めでもらったロキソニン飲んじゃおうかな。食道の痛さにも効くのかな。
"""

model_inputs = tokenizer(inputs, return_tensors="pt", padding='max_length', max_length=512, truncation=True)

output = model.inference(
    input_ids=model_inputs['input_ids'], 
    attention_mask=model_inputs['attention_mask'],
    memory=None,
    max_new_tokens=300,
    do_sample=False,
)

In [29]:
output

(tensor([[    2,     0,  8611,    92, 12410,   140,     4,  8611,  1463,    52,
              8,     5,  8611,   147, 12410,   140,     5,  8611,    92,  8847,
             37,   140,     4,  1463,     8,  8611,   124, 12410,   140,    10,
            148,     6,  8611,    69, 12410,   140,     8,     5,  1293,     8,
           8611,    22,    15,   140,     5,    92,    15,   140,     8,  8611,
             69,    15,   140,     4,     5,   227,   619,     8,  8611,    49,
             15,   140,    10,   118,     6,     2]]),
 tensor([[[-0.2825,  0.0153,  0.4446,  ..., -0.1582,  0.2357,  0.8595],
          [-0.3044,  0.0067, -0.0658,  ...,  0.0645,  0.5732,  0.1090],
          [-0.4471,  0.7371, -0.0711,  ...,  0.1462,  0.8290,  0.6467],
          ...,
          [-1.2815,  0.4026, -0.5653,  ...,  0.2735,  0.3208,  0.7414],
          [-0.9321, -0.0389,  0.1910,  ...,  0.7977,  0.8452,  0.4022],
          [-0.1103,  0.3367, -0.3702,  ...,  0.1602,  0.1236, -0.0320]]]))

In [30]:
print(tokenizer.batch_decode(output[0], skip_special_tokens=True))

['妊娠 ５ カ月 まで の 妊娠 期間 中 は 、 妊娠 ７ カ月 まで 、 妊娠 ５ ヵ 月 まで の 期間 は 妊娠 ６ カ月 まで と なる 。 妊娠 ４ カ月 まで は 、 通常 は 妊娠 ２ 年 まで 、 ５ 年 まで は 妊娠 ４ 年 まで の 、 それ 以降 は 妊娠 ３ 年 まで と なった 。']


In [31]:
# TODO: 写一个无限长度的segment测试ROUGE指标

import pandas as pd
from datasets import Dataset
data_frame = pd.read_json('datasets/tobyoki/tobyoki-event_summary_juman_processed_grouped.json', orient='records', encoding='utf-8', lines=False)

raw_datasets = Dataset.from_pandas(data_frame)
raw_datasets = raw_datasets.train_test_split(test_size=0.1, seed=42)
temp = raw_datasets['train'].train_test_split(test_size=0.1/(0.8+0.1), seed=42)
raw_datasets['train'], raw_datasets['validation'] = temp['train'], temp['test']
raw_datasets['test'].remove_columns(['user', 'summary'])

Dataset({
    features: ['text', 'incremental_summary'],
    num_rows: 10
})

In [32]:
# 递归的读取raw_datasets['test']的每一行
data_column = raw_datasets['test']['text']
target_column = raw_datasets['test']['incremental_summary']

data_column[0], target_column[0]

(['2023 - 02 - 09 \n 2023 . 2 . 8 乳 がん 検診 \n 市 の 無料 クーポン を 使って 、 乳 がん 検診 へ 。 行こう 行こう と 思い ながら 、 だらだら と 延ばして しまって いた 。 気 に なる の は 、 左 胸 の 表面 に ボコボコ と 固い もの が 触れる こと 。 生理 前 に 痛み が ある ので 、 乳腺 症 ？ と 思って いた のだ けど 。 まず エコー 。 左 胸 の エコー が やたら 長い 写真 も めっちゃ 撮る し 、 黒い 楕円 形 の もの を 何度 も 計測 して いる 。 とても 念入りに 。 右胸 は その 1 / 3 くらい の 時間 だった 。 次に マンモグラフィ 。 想像 より 痛く なかった 。 技師 さん も 看護 師 さん も 、 胸 の こと 「 お 胸 」 と 言う の が 少し ふふっと なった 。 診察 。 左 胸 に しこり が ある 。 左 の 脇 に も 腫れ が ある 。 しこり は 花火 の ように ギザギザ して いる 。 良い もの か 悪い もの か 、 組織 診 を し ましょう と 。 明るい 診察 室 で 上半身 裸 に なる の は さすが に 抵抗 が あった けど 、 言わ れる が まま に 。 ここ に いる 人 たち に とって は 日常 。 消毒 して 局所 麻酔 して 、 バン ！ と 2 回 。 バネ 式 な の ね 。 痛み は なかった 。 結果 は 来週 。 その後 圧迫 する も 、 出血 が なかなか 止まら ず で 、 ステリテープ を 貼って もらい 、 圧迫 ガーゼ も そのまま で 帰宅 。 明日 傷 を 見せ に きて って 。 パート だ けど 、 有休 ある し 休んじゃ った こういう 時 の 有休 だ よ ね ！ がん だったら 、 手術 、 入院 、 化学 療法 ？ 腋窩 の リンパ に 転移 して いたら ‥ 入院 中 、 子供 は ？ パート は 休職 できる か な ？ お 金 、 大丈夫 か な 、 これ から 子供 達 お 金 かかる のに 。 気づいたら いろいろ 考えて しまう ので 、 ここ に 記録 する こと に し ます ！',
  '2023 - 02 - 

In [33]:
import numpy as np
import evaluate 

metric = evaluate.load('rouge')

def compute_metrics(preds, labels):
    preds, labels = preds, labels
    if isinstance(preds, tuple): 
        preds = preds[0]
    # Replace -100s used for padding as we can't decode them
    # preds = np.where(preds != -100, preds, tokenizer.pad_token_id)
    # decoded_preds = tokenizer.batch_decode(preds, skip_special_tokens=True)
    # labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    # decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)

    # Some simple post-processing
    preds, labels = postprocess_text(preds, labels)
    # print(f'decoded_preds: {decoded_preds}')
    # print(f'decoded_labels: {decoded_labels}')
    
    result = metric.compute(predictions=preds, references=labels, 
                            tokenizer=lambda x: x.split(), use_stemmer=True)
    result = {k: round(v * 100, 4) for k, v in result.items()}
    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in preds]
    result["gen_len"] = np.mean(prediction_lens)
    return result

def postprocess_text(preds, labels):
    # sent_detector = nltk.RegexpTokenizer(u'[^　！？。]*[！？。.\n]')
    
    preds = [pred.strip() for pred in preds]
    labels = [label.strip() for label in labels]

    # preds = ["\n".join(sent_detector.tokenize(pred)) for pred in preds]
    # labels = ["\n".join(sent_detector.tokenize(label)) for label in labels]
    
    # rougeLSum expects newline after each sentence
    # preds = ["\n".join(nltk.sent_tokenize(pred)) for pred in preds]
    # labels = ["\n".join(nltk.sent_tokenize(label)) for label in labels]
    
    import functools
    from ja_sentence_segmenter.common.pipeline import make_pipeline
    from ja_sentence_segmenter.concatenate.simple_concatenator import concatenate_matching
    from ja_sentence_segmenter.normalize.neologd_normalizer import normalize
    from ja_sentence_segmenter.split.simple_splitter import split_newline, split_punctuation

    split_punc2 = functools.partial(split_punctuation, punctuations=r"．。!?.")
    # concat_tail_no = functools.partial(concatenate_matching, former_matching_rule=r"^(?P<result>.+)(の)$", remove_former_matched=False)
    segmenter = make_pipeline(split_punc2)

    preds = ["\n".join(list(segmenter(pred))) for pred in preds]
    labels = ["\n".join(list(segmenter(label))) for label in labels]
    
    # print(f'{preds=}')
    # print(f'{labels=}')
    return preds, labels

In [34]:
from tqdm import tqdm
predictions = []
labels = []

for segments, targets in tqdm(zip(data_column, target_column)):
    memory = None
    for segment, target in zip(segments, targets):
        model_inputs = tokenizer(segment, return_tensors="pt", padding='max_length', max_length=512, truncation=True)
        output = model.inference(
            input_ids=model_inputs['input_ids'], 
            attention_mask=model_inputs['attention_mask'],
            memory=memory,
            max_new_tokens=300,
            do_sample=True,
        )
        memory = output[1]
        prediction = tokenizer.batch_decode(output[0], skip_special_tokens=True)[0]
        
        predictions.append(prediction)
        labels.append(target)

3it [24:44, 481.26s/it]

In [ ]:
result = compute_metrics(predictions, labels)
result 

{'rouge1': 7.9611,
 'rouge2': 0.6271,
 'rougeL': 5.0267,
 'rougeLsum': 7.7316,
 'gen_len': 1.0}

In [3]:
import pandas as pd
from datasets import load_dataset

raw_datasets = load_dataset(
    "json",
    data_dir="datasets/tobyoki",
)

Generating train split: 100 examples [00:00, 217.03 examples/s]


In [6]:
raw_datasets['train']['text']


[['2014 - 01 - 10 \n 告知 \n 2013 年 12 月 、 手術 検査 の 結果 を 聞き に 病院 へ 。 「 残念です が 、 乳 がん です 。 」 本当に 「 残念です が ・ ・ ・ 」 って 言う んだ～ が 最初の 感想 。 「 ステージ ０ の 初期 です が 、 治療 と して は 手術 で 左 乳房 を 全摘 し ます 。 温存 は 出来 ませ ん 。 」 ・ ・ ・ 。 おっぱい 、 とっちゃ う の ？ ？ ？ ここ から 先 は 、 ほとんど 覚えて ませ ん 。 きっつい なぁ～ こんな 思い しか 出て こ なかった ・ ・ ・',
  '2014 - 01 - 14 \n 手術 は イヤ ！ \n 告知 から 数 日 、 頭 の 中 は 病気 の こと ばかり 。 気 が つけば 、 涙 も 出て くる 。 乳房 再建 に ついて インターネット で 調べて も よく わから ない 。 体験 者 の 話 は 、 イヤな 部分 だけ 目 に 付く 。 こんな 中 で 衝動 的に パパ に 話した の は 、 「 手術 は 受け ない ！ 」 でした 。 みんな 、 チビ の ため って 言う けど 、 母親 を 必要 と する の は 後 何 年間 の 話 ？ それ から 先 の 数十 年 で 、 私 は 手術 を 受けた こと を 後悔 し ない の ？ 費用 だって たくさん 掛かる なら 、 その分 チビ の 将来 に まわした ほう が ・ ・ ・ そんな モヤモヤ した 気持ち が 溜まって ・ ・ ・ パパ は 黙って 聞いて くれ ました 。 「 どう する か は 自分 で 決め なさい 。 」 私 は 本当 は どう し たい の か な ・ ・ ・',
  '2014 - 01 - 17 \n 最悪の 大晦日 \n 12 月 31 日 に 家族 で 私 の 実家 に 帰省 。 病気 が わかって から 初めて の 帰省 な ので 、 ここ で 両親 と 病気 に ついて 話し ました 。 反応 、 うすっ ！ ！ ∑(ﾟДﾟ) 「 で 、 手術 は いつ ？ 当日 行って も ヒマだ から 、 落ち着いたら お 見舞い に 行く よ 」 だって ・ ・ ・ 娘 が ガン の 手術 だって いう 